In [1]:
import sklearn.datasets
import pandas as pd
import numpy as np
import torch
from time import time
from os.path import join
import umap
import umap.plot
import matplotlib.pylab as plt
savedir = r"E:\OneDrive - Harvard University\CNN-PCs"
feattsr_penult = torch.load(join(savedir, "resnet50_swsl_INvalid_penult_feattsrs.pt"))
feattsrs = torch.load(join(savedir, "resnet50_swsl_INvalid_feattsrs.pt"))

In [2]:
t0 = time()
mapper = umap.UMAP(metric="cosine", n_neighbors=40).fit(feattsr_penult)  #
print("%.2f sec " % (time() - t0))

43.25 sec 


In [3]:
t0 = time()
mapper4 = umap.UMAP(metric="cosine", n_neighbors=40).fit(feattsrs['.layer4.Bottleneck2'].numpy())  #
print("%.2f sec " % (time() - t0))

33.68 sec 


In [4]:
t0 = time()
mapper3 = umap.UMAP(metric="cosine", n_neighbors=40).fit(feattsrs['.layer4.Bottleneck0'].numpy())  #
print("%.2f sec " % (time() - t0))

32.24 sec 


In [5]:
t0 = time()
mapper2 = umap.UMAP(metric="cosine", n_neighbors=40).fit(feattsrs['.layer3.Bottleneck5'].numpy())  #
print("%.2f sec " % (time() - t0))

28.03 sec 


In [6]:
t0 = time()
mapper1 = umap.UMAP(metric="cosine", n_neighbors=40).fit(feattsrs['.layer2.Bottleneck3'].numpy())  #
print("%.2f sec " % (time() - t0))

26.94 sec 


In [ ]:
ax = umap.plot.points(mapper, values=feattsr_penult[:, 2000],
                      width=2500, height=2500, cmap="Blues")
plt.show()

In [12]:
from scipy.stats import ttest_rel, ttest_ind

def laplace_operator(graph_, activvect):
    if activvect.ndim == 2:
        sumact = np.array(graph_.sum(axis=1))[:, :] * activvect
    elif activvect.ndim == 1:
        sumact = np.array(graph_.sum(axis=1))[:, 0] * activvect
    transact = (graph_@activvect)
    lpls_val = transact - sumact
    return lpls_val

In [11]:
feattsrs['.layer3.Bottleneck5'].numpy().ndim

2

In [32]:

lpls_dict = {}
actlayer = '.layer3.Bottleneck5'
for actlayer in feattsrs.keys():
    actmat = feattsrs[actlayer].numpy()
    print("Activation of ", actlayer)
    for mapr, label in zip([mapper, mapper4, mapper3, mapper2, mapper1, ],
                           ["penult", "layer4.B2", "layer4.B0", "layer3.B5", "layer2.B3"]):
        lpls_mat= laplace_operator(mapr.graph_, actmat)
        lpls_mat_shfl = laplace_operator(mapr.graph_, np.random.permutation(actmat))
        lpls_dict[(actlayer, label)] = (lpls_mat, lpls_mat_shfl)
        lpls_abs_m = np.abs(lpls_mat).mean(axis=1)
        lpls_pow_m = np.square(lpls_mat).mean(axis=1)
        shfl_abs_m = np.abs(lpls_mat_shfl).mean(axis=1)
        shfl_pow_m = np.square(lpls_mat_shfl).mean(axis=1)
        tval_ab, pval_ab = ttest_rel(lpls_abs_m, shfl_abs_m)
        tval_sq, pval_sq = ttest_rel(lpls_pow_m, shfl_pow_m)
        print("Disstance matrix based on layer", label, "activation of ", actlayer)
        print(f"Laplace - Shuffle \nAbs: {lpls_abs_m.mean():.2f} - {shfl_abs_m.mean():.2f} {tval_ab:.3f} (P={pval_ab:.1e})   "
              f"\nSquared: {lpls_pow_m.mean():.2f} - {shfl_pow_m.mean():.2f} {tval_sq:.3f} (P={pval_sq:.1e})")

Activation of  .layer2.Bottleneck3
Disstance matrix based on layer penult activation of  .layer2.Bottleneck3
Laplace - Shuffle 
Abs: 6.10 - 6.30 -32.701 (P=4.3e-232)   
Squared: 104.48 - 108.93 -12.626 (P=1.7e-36)
Disstance matrix based on layer layer4.B2 activation of  .layer2.Bottleneck3
Laplace - Shuffle 
Abs: 6.13 - 6.40 -41.781 (P=0.0e+00)   
Squared: 110.20 - 116.91 -14.686 (P=1.0e-48)
Disstance matrix based on layer layer4.B0 activation of  .layer2.Bottleneck3
Laplace - Shuffle 
Abs: 6.00 - 6.39 -55.963 (P=0.0e+00)   
Squared: 103.59 - 114.72 -26.374 (P=3.0e-152)
Disstance matrix based on layer layer3.B5 activation of  .layer2.Bottleneck3
Laplace - Shuffle 
Abs: 5.58 - 6.61 -96.267 (P=0.0e+00)   
Squared: 112.52 - 180.31 -13.957 (P=3.4e-44)
Disstance matrix based on layer layer2.B3 activation of  .layer2.Bottleneck3
Laplace - Shuffle 
Abs: 4.19 - 6.75 -180.526 (P=0.0e+00)   
Squared: 53.22 - 171.62 -41.097 (P=0.0e+00)
Activation of  .layer3.Bottleneck5
Disstance matrix based on 

In [30]:
lpls_abs_m = np.abs(lpls_mat).mean(axis=1)
lpls_pow_m = np.square(lpls_mat).mean(axis=1)
shfl_abs_m = np.abs(lpls_mat_shfl).mean(axis=1)
shfl_pow_m = np.square(lpls_mat_shfl).mean(axis=1)
tval_ab, pval_ab = ttest_rel(lpls_abs_m, shfl_abs_m)
tval_sq, pval_sq = ttest_rel(lpls_pow_m, shfl_pow_m)
print(f"Laplace - Shuffle \nAbs: {lpls_abs_m.mean():.2f} - {shfl_abs_m.mean():.2f} {tval_ab:.3f} (P={pval_ab:.1e})   "
      f"\nSquared: {lpls_pow_m.mean():.2f} - {shfl_pow_m.mean():.2f} {tval_sq:.3f} (P={pval_sq:.1e})")

Laplace - Shuffle 
Abs: 2.80 - 3.15 -111.517 (P=0.0e+00)   
Squared: 36.10 - 41.92 -37.630 (P=1.3e-305)


In [17]:
np.random.permutation?

In [121]:
activvect = feattsrs['.layer3.Bottleneck5'][:, 100].numpy()

In [123]:
lpls_val = laplace_operator(mapper.graph_, activvect)
print("Original (embed layer4): mean abs", np.abs(lpls_val).mean(), 
      "mean squ",  np.square(lpls_val).mean())
lpls_val_shfl = laplace_operator(mapper.graph_, np.random.permutation(activvect))
print("Shuffled (embed layer4): mean abs", np.abs(lpls_val_shfl).mean(), 
      "mean squ",  np.square(lpls_val_shfl).mean())

lpls_val = laplace_operator(mapper2.graph_, activvect)
print("Original (embed layer3): mean abs", np.abs(lpls_val).mean(), 
      "mean squ",  np.square(lpls_val).mean())
lpls_val_shfl = laplace_operator(mapper2.graph_, np.random.permutation(activvect))
print("Shuffled (embed layer3): mean abs", np.abs(lpls_val_shfl).mean(), 
      "mean squ",  np.square(lpls_val_shfl).mean())

lpls_val = laplace_operator(mapper3.graph_, activvect)
print("Original (embed layer2): mean abs", np.abs(lpls_val).mean(), 
      "mean squ",  np.square(lpls_val).mean())
lpls_val_shfl = laplace_operator(mapper3.graph_, np.random.permutation(activvect))
print("Shuffled (embed layer2): mean abs", np.abs(lpls_val_shfl).mean(), 
      "mean squ",  np.square(lpls_val_shfl).mean())

Original (embed layer4): mean abs 0.8584047 mean squ 19.123417
Shuffled (embed layer4): mean abs 1.0142239 mean squ 24.646997
Original (embed layer3): mean abs 0.49748853 mean squ 5.382636
Shuffled (embed layer3): mean abs 1.085481 mean squ 36.068554
Original (embed layer2): mean abs 0.86236024 mean squ 19.412672
Shuffled (embed layer2): mean abs 1.1432737 mean squ 53.31533


In [7]:
umap.plot.output_notebook()

Loading BokehJS ...

In [38]:
p = umap.plot.interactive(mapper, values=feattsrs['.layer3.Bottleneck5'][:, 500].numpy(), point_size=1.5, alpha=.7)
p.title = "UMap with fc input, Color value showing Layer3.B5"
umap.plot.show(p)

In [39]:
p = umap.plot.interactive(mapper2, values=feattsrs['.layer3.Bottleneck5'][:, 500].numpy(), point_size=1.5, alpha=.7)
p.title = "UMap with Layer3.B5, Color value showing Layer3.B5"
umap.plot.show(p)

In [37]:
p = umap.plot.interactive(mapper2, values=feattsrs['.layer2.Bottleneck3'][:, 500].numpy(), point_size=1.5, alpha=.7)
p.title = "UMap with Layer3.B5, Color value showing Layer2.B3"
umap.plot.show(p)

In [31]:
p = umap.plot.interactive(mapper, values=feattsrs['.layer2.Bottleneck3'][:, 500].numpy(), 
                          point_size=1.5, alpha=.7)
umap.plot.show(p)

In [71]:
activvect = feattsrs['.layer2.Bottleneck3'][:, 500].numpy()

In [35]:
np.array(mapper.graph_.sum(axis=1))[:, 0].shape

(50000,)

In [42]:
sumact = np.array(mapper.graph_.sum(axis=1))[:, 0] * activvect
transact = (mapper.graph_@activvect)
lpls_val = transact - sumact

In [46]:
print("mean abs", np.abs(lpls_val).mean(), 
"mean squ",  np.square(lpls_val).mean())

mean abs 4.9707346 mean squ 67.41414


In [ ]:
mapper.graph_@activvect - mapper.graph_.sum(axis=1)*activvect

In [4]:
%matplotlib inline